# Household Debt-to-income Ratios by county

#### This project is going to evaluate debt-to-income ratios by county. A visualization of the change over time can be found at https://www.federalreserve.gov/releases/z1/dataviz/household_debt/county/map/#state:all;year:2016, so this project will seek to answer a different question: in what counties has the debt-to-income ratio changed the *most* since 1999?

### Import Libraries

In [249]:
import pandas as pd
from ydata_profiling import ProfileReport
import numpy as np
pd.set_option('display.max_rows', None)

I always suggest starting your EDA with a ProfileReport from the ydata_profiling package

In [250]:
df = pd.read_csv('data/household-debt-by-county.csv')
report = ProfileReport(df, tsmode=True, sortby="year")

In [42]:
report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

: 

: 

## What now?

### What to do with these missing values?

- For the missing values in the "high" category, we will be imputing the mean of the previous three years. This will be a simple solution that will quickly allow us to move forward with using the data to gain insight into what counties are most effected by the debt-to-income gap while also accounting for variability that may exist over the past few years of data.

In [254]:
df = df.sort_values(by=['area_fips', 'year', 'qtr'])

#### Impute our missing values for the "high" column

In [255]:
rolling_mean = df.groupby("area_fips")["high"].transform(lambda x: x.rolling(12, min_periods=1).mean())

In [256]:
for index, data in df.iterrows():
    if pd.isna(data['high']):
        df.at[index, "high"] = rolling_mean[index]

In [257]:
report = ProfileReport(df, tsmode=True, sortby="year")
report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

- Even after imputing data, we still have ~6% missing cells in the "high" column. Let's take a look and see what could be going on

In [258]:
print(df[df.isna().any(axis=1)])

        year  qtr  area_fips   low  high
94110   2006    3       1001  3.43   NaN
97248   2006    4       1001  3.43   NaN
100386  2007    1       1001  3.43   NaN
103524  2007    2       1001  3.43   NaN
106662  2007    3       1001  3.43   NaN
109799  2007    4       1001  3.43   NaN
112936  2008    1       1001  3.43   NaN
116073  2008    2       1001  3.43   NaN
119210  2008    3       1001  3.43   NaN
122345  2008    4       1001  3.43   NaN
125480  2009    1       1001  3.43   NaN
128616  2009    2       1001  3.43   NaN
131752  2009    3       1001  3.43   NaN
134888  2009    4       1001  3.43   NaN
138024  2010    1       1001  3.43   NaN
141160  2010    2       1001  3.43   NaN
144299  2010    3       1001  3.43   NaN
147440  2010    4       1001  3.43   NaN
150581  2011    1       1001  3.43   NaN
153723  2011    2       1001  3.43   NaN
156865  2011    3       1001  3.43   NaN
160007  2011    4       1001  3.43   NaN
163147  2012    1       1001  3.43   NaN
166286  2012    

- It looks like the missing rows have in common that they are the same counties
- There is no way of knowing how these cells ended up missing. Because imputing these values may lead to misunderstanding the data, we are going to throw the missing values out of our dataset. 

In [260]:
df.dropna(inplace=True)

In [262]:
report = ProfileReport(df, tsmode=True, sortby="year")
report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### What do these fips codes mean?
- The next step will be to connect these seemingly random fips codes to a map.
- This will allow us to see how the household debt differences have changed over the years